<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Data Visualization Workflow

In this workflow within PyCCAPT, we can crop the data, do the voltage and bowl calibration, calculate the 3d reconstruction, and do the ranging.
</div>

In [1]:
# Activate intractive functionality of matplotlib
%matplotlib ipympl
# Activate auto reload 
%load_ext autoreload
%autoreload 2
%reload_ext autoreload
# import libraries
import os
import numpy as np
import subprocess
from ipywidgets import widgets
from IPython.display import display
from ipywidgets import fixed, interact_manual
import warnings
# Ignore all warnings
warnings.filterwarnings("ignore")

# Local module and scripts
from pyccapt.calibration.calibration import widgets as wd
from pyccapt.calibration.data_tools import data_tools
from pyccapt.calibration.tutorials.tutorials_helpers import helper_data_loader
from pyccapt.calibration.tutorials.tutorials_helpers import helper_visualization
from pyccapt.calibration.calibration import share_variables
from pyccapt.calibration.calibration import ion_selection

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In case of recieving the error about pytable library, you have to install the pytables library with conda command. to do that you can open a new cell and copy the line below in it. Then just run it like other cells. The pytables library will be innstalled.
    
`!conda install --yes --prefix {sys.prefix} pytables`
</div>


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In the cell below we create variable object. This object is used in many of the functions to share the data between functions in as easy way. 
</div>


In [2]:
variables = share_variables.Variables()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
By clicking on the button below, you can select the dataset file you want to crop. The dataset file can be in various formats, including HDF5, EPOS, POS, ATO, and CSV. The cropped data will be saved in the same directory as the original dataset file in a new directory nammed load_crop. The name of the cropped dataset file will be the same as the original dataset file. The figures will be saved in the same directory as the dataset file.
</div>

In [3]:
button = widgets.Button(description='load dataset')

@button.on_click
def open_file_on_click_r(b):
    global dataset_path
    folder_path = variables.last_directory
    script = '..//..//data_tools//run_dataset_path_qt.py'
    cmd = f"python {script} {folder_path}"
    result = subprocess.run(cmd, capture_output=True, text=True, shell=True)
    dataset_path = result.stdout.strip()
    variables.last_directory = dataset_path

button

Button(description='load dataset', style=ButtonStyle())

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## ROI Selection and Data Cropping
    

</div>



<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

    
From the dropdown lists below, you can select the instrument specifications of the dataset. The instrument specifications are the same as the ones used for the calibration process. Data mode is specify the dataset structure. The dataset can be in raw or calibrated mode. The flight path length is the distance between the sample and the detector. The t0 is the time of flight of the ions with the lowest mass-to-charge ratio. The maximum mass-to-charge ratio is the maximum mass-to-charge ratio of tat you want to plot. You can also change it in te related cells. The detector diameter is the diameter of the detector.
</div>


In [5]:
# create an object for selection of instrument specifications of the dataset
tdc, pulse_mode, flight_path_length, t0, max_mc, det_diam = wd.dataset_instrument_specification_selection()

# Display lists and comboboxes to selected instrument specifications
display(tdc, pulse_mode, flight_path_length, t0, max_mc)

Dropdown(description='Data mode:', options=('pyccapt', 'leap_epos', 'leap_pos', 'leap_apt', 'ato_v6'), value='…

Dropdown(description='Pulse mode:', options=('voltage', 'laser'), value='voltage')

FloatText(value=110.0, description='Flight path length:')

FloatText(value=38.0, description='t0:')

FloatText(value=400.0, description='Max mc:')

In [7]:
helper_data_loader.load_data(dataset_path, max_mc.value, flight_path_length.value, pulse_mode.value, tdc.value, variables, processing_mode=False)
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
display(variables.data)
display(variables.range_data)

The data will be saved on the path: T:/Ortner/03_APT/Oxcart/2454_Apr-07-2025_10-19_NiC2_6082-65min/2454_Apr-07-2025_10-19_NiC2_6082-65min/data_processing/2454_Apr-07-2025_10-19_NiC2_6082-65min/visualization/
The dataset name after saving is: 2454_Apr-07-2025_10-19_NiC2_6082-65min
The figures will be saved on the path: T:/Ortner/03_APT/Oxcart/2454_Apr-07-2025_10-19_NiC2_6082-65min/2454_Apr-07-2025_10-19_NiC2_6082-65min/data_processing/2454_Apr-07-2025_10-19_NiC2_6082-65min/visualization/
Total number of Ions: 22157254
The maximum possible time of flight is: 5010


x (nm)  y (nm)  z (nm)     mc (Da)  mc_uc (Da)  high_voltage (V)  \
0            0.0     0.0     0.0   27.981170   31.785536         2232.5865   
1            0.0     0.0     0.0   27.434791   31.326274         2232.5865   
2            0.0     0.0     0.0   27.408784   31.120324         2232.5865   
3            0.0     0.0     0.0  382.462302  445.438904         2231.6625   
4            0.0     0.0     0.0   27.372068   31.128182         2231.6625   
...          ...     ...     ...         ...         ...               ...   
22157249     0.0     0.0     0.0   27.248027   30.878184         5601.2285   
22157250     0.0     0.0     0.0   26.959221   29.493772         5601.2285   
22157251     0.0     0.0     0.0   26.969435   30.591035         5601.2285   
22157252     0.0     0.0     0.0   26.999729   29.604551         5601.2285   
22157253     0.0     0.0     0.0   27.495170   30.070710         5601.2285   

          pulse_v (V)  pulse_l (pJ)       t (ns)     t_c (ns)  x_det (cm)  \
0            446.5173           0.0   944.017416   944.017416    2.481633   
1            446.5173           0.0   937.858932   937.858932    2.331429   
2            446.5173           0.0   934.258482   934.258482    2.471837   
3            446.3325           0.0  3334.167576  3334.167576   -0.336327   
4            446.3325           0.0   923.704020   923.704020    1.753469   
...               ...           ...          ...          ...         ...   
22157249    1120.2457           0.0   596.021922   596.021922   -0.055510   
22157250    1120.2457           0.0   580.029066   580.029066    0.894694   
22157251    1120.2457           0.0   594.019386   594.019386   -0.120816   
22157252    1120.2457           0.0   580.015350   580.015350    0.790204   
22157253    1120.2457           0.0   585.241146   585.241146    0.839184   

          y_det (cm)     delta_p  multi  start_counter  
0           0.561633           0      1          19612  
1           1.071020          65      1          19677  
2           0.535510          10      1          19687  
3          -0.084898  4294947915      1            306  
4           0.493061         122      1            428  
...              ...         ...    ...            ...  
22157249    1.786122         575      1           8171  
22157250   -0.907755           3      1           8174  
22157251    1.854694          10      1           8184  
22157252   -0.731429          11      1           8195  
22157253   -0.953469           2      1           8197  

[22157254 rows x 15 columns]

name ion  mass   mc  mc_low  mc_up    color     element complex  \
0  unranged0  un   0.0  0.0     0.0  400.0  #000000  [unranged]     [0]   

  isotope  charge  
0     [0]       0

<div style="margin: 0 auto; padding: 20px;">

Load a pre saved range file if you want from cell below
</div>


In [7]:
button_r = widgets.Button(description='load range dataset')

@button_r.on_click
def open_file_on_click_r(b):
    global range_path
    folder_path = variables.last_directory
    script = '..//..//data_tools//run_dataset_path_qt.py'
    cmd = f"python {script} {folder_path}"
    result = subprocess.run(cmd, capture_output=True, text=True, shell=True)
    range_path = result.stdout.strip()

button_r

Button(description='load range dataset', style=ButtonStyle())

In [8]:
if 'range_path' in globals():
    variables.range_data = data_tools.read_range(range_path)

In [9]:
display(variables.range_data.style.applymap(ion_selection.display_color, subset=['color']))

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the range in the hdf5 and csv format.

</div>

In [ ]:
interact_manual_range = interact_manual.options(manual_name="save range")
interact_manual_range(data_tools.save_range, variables=fixed(variables));

In [10]:
variables.data

x (nm)  y (nm)  z (nm)     mc (Da)  mc_uc (Da)  high_voltage (V)  \
0            0.0     0.0     0.0   27.981170   31.785536         2232.5865   
1            0.0     0.0     0.0   27.434791   31.326274         2232.5865   
2            0.0     0.0     0.0   27.408784   31.120324         2232.5865   
3            0.0     0.0     0.0  382.462302  445.438904         2231.6625   
4            0.0     0.0     0.0   27.372068   31.128182         2231.6625   
...          ...     ...     ...         ...         ...               ...   
22157249     0.0     0.0     0.0   27.248027   30.878184         5601.2285   
22157250     0.0     0.0     0.0   26.959221   29.493772         5601.2285   
22157251     0.0     0.0     0.0   26.969435   30.591035         5601.2285   
22157252     0.0     0.0     0.0   26.999729   29.604551         5601.2285   
22157253     0.0     0.0     0.0   27.495170   30.070710         5601.2285   

          pulse_v (V)  pulse_l (pJ)       t (ns)     t_c (ns)  x_det (cm)  \
0            446.5173           0.0   944.017416   944.017416    2.481633   
1            446.5173           0.0   937.858932   937.858932    2.331429   
2            446.5173           0.0   934.258482   934.258482    2.471837   
3            446.3325           0.0  3334.167576  3334.167576   -0.336327   
4            446.3325           0.0   923.704020   923.704020    1.753469   
...               ...           ...          ...          ...         ...   
22157249    1120.2457           0.0   596.021922   596.021922   -0.055510   
22157250    1120.2457           0.0   580.029066   580.029066    0.894694   
22157251    1120.2457           0.0   594.019386   594.019386   -0.120816   
22157252    1120.2457           0.0   580.015350   580.015350    0.790204   
22157253    1120.2457           0.0   585.241146   585.241146    0.839184   

          y_det (cm)     delta_p  multi  start_counter  
0           0.561633           0      1          19612  
1           1.071020          65      1          19677  
2           0.535510          10      1          19687  
3          -0.084898  4294947915      1            306  
4           0.493061         122      1            428  
...              ...         ...    ...            ...  
22157249    1.786122         575      1           8171  
22157250   -0.907755           3      1           8174  
22157251    1.854694          10      1           8184  
22157252   -0.731429          11      1           8195  
22157253   -0.953469           2      1           8197  

[22157254 rows x 15 columns]

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the dataset in any other format that you want.

</div>

In [32]:
interact_manual_data = interact_manual.options(manual_name="save data")
interact_manual_data(data_tools.save_data, data=fixed(variables.data), variables=fixed(variables),
                name=widgets.Text(value=variables.result_data_name),
                hdf=widgets.Dropdown(options=[('True', True), ('False', False)]),
                epos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                pos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                ato_6v=widgets.Dropdown(options=[('False', False), ('True', True)]),
                csv=widgets.Dropdown(options=[('False', False), ('True', True)]),
               temp=fixed(False));

interactive(children=(Text(value='R5096_92775_C4', continuous_update=False, description='name'), Dropdown(desc…

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
# Visualization
    
</div>

In [34]:
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

The maximum possible time of flight is: 5010


In [26]:
helper_visualization.call_visualization(variables)

In [ ]:
from pyccapt.calibration.calibration import mc_plot
hist = variables.data['mc (Da)'].to_numpy()
mc_hist = mc_plot.AptHistPlotter(hist[hist < 40], variables)
mc_hist.plot_histogram(bin_width=0.1, label='mc', steps='stepfilled', log=True)
mc_hist.find_peaks_and_widths()
mc_hist.plot_hist_info_legend(loc='right')
mc_hist.plot_line_hist()
mc_hist.manual_background_fit()

In [ ]:
variables.plotly_3d_reconstruction

In [ ]:
from IPython.display import display, HTML
display(HTML(variables.animation_detector_html))